# <p style="padding:15px; background-color:#2D3142; font-family:JetBrains Mono; font-weight:bold; color:#f2f2f0; font-size:100%; letter-spacing: 2px; text-align:center; border-radius: 10px 10px">Playground Series S3E15</p>

In [1]:
# %load ../initial_settings2.py
import os
import shutil
import subprocess
import sys
import warnings
from pathlib import Path

ON_KAGGLE = os.getenv("KAGGLE_KERNEL_RUN_TYPE") is not None
if ON_KAGGLE:
    warnings.filterwarnings("ignore")
    os.environ["TF_CPP_MIN_LOG_LEVEL"] = "3"

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns
import tensorflow as tf
import tensorflow_datasets as tfds

# Sub-modules and so on.
from colorama import Fore, Style
from IPython.core.display import HTML
from IPython.display import display_html
from keras import layers
from plotly.subplots import make_subplots
from tensorflow import keras

K = keras.backend

# Colorama settings.
CLR = (Style.BRIGHT + Fore.BLACK) if ON_KAGGLE else (Style.BRIGHT + Fore.WHITE)
RED = Style.BRIGHT + Fore.RED
BLUE = Style.BRIGHT + Fore.BLUE
CYAN = Style.BRIGHT + Fore.CYAN
RESET = Style.RESET_ALL

# Colors
DF_CMAP = sns.light_palette("#8C92AC", as_cmap=True)
FONT_COLOR = "#141B4D"
BACKGROUND_COLOR = "#F6F5F5"
NOTEBOOK_PALETTE = {
    "Coral": "#FF7F51",
    "DarkNavy": "#2D3142",
    "SlateBlue": "#8C92AC",
}
MY_RC = {
    "axes.labelcolor": FONT_COLOR,
    "axes.labelsize": 10,
    "axes.labelpad": 15,
    "axes.labelweight": "bold",
    "axes.titlesize": 14,
    "axes.titleweight": "bold",
    "axes.titlepad": 15,
    "xtick.labelsize": 10,
    "xtick.color": FONT_COLOR,
    "ytick.labelsize": 10,
    "ytick.color": FONT_COLOR,
    "figure.titlesize": 14,
    "figure.titleweight": "bold",
    "figure.facecolor": BACKGROUND_COLOR,
    "figure.edgecolor": BACKGROUND_COLOR,
    "figure.dpi": 72,  # Locally Seaborn uses 72, meanwhile Kaggle 96.
    "font.size": 10,
    "font.family": "Serif",
    "text.color": FONT_COLOR,
}

sns.set_theme(rc=MY_RC)


# Utility functions.
def download_dataset_from_kaggle(user, dataset, directory):
    command = "kaggle datasets download -d "
    filepath = directory / (dataset + ".zip")

    if not filepath.is_file():
        subprocess.run((command + user + "/" + dataset).split())
        filepath.parent.mkdir(parents=True, exist_ok=True)
        shutil.unpack_archive(dataset + ".zip", "data")
        shutil.move(dataset + ".zip", "data")


def download_competition_from_kaggle(competition):
    command = "kaggle competitions download -c "
    filepath = Path("data/" + competition + ".zip")

    if not filepath.is_file():
        subprocess.run((command + competition).split())
        Path("data").mkdir(parents=True, exist_ok=True)
        shutil.unpack_archive(competition + ".zip", "data")
        shutil.move(competition + ".zip", "data")


# Html `code` block highlight.
HTML(
    """
<style>
code {
    background: rgba(42, 53, 125, 0.10) !important;
    border-radius: 4px !important;
}
</style>
"""
)


<b><span style="font-size:20px; font-family:JetBrains Mono; margin-left: 5px;">
    Competition Description 📜
</span></b>
<p style="font-size:16px;font-family: JetBrains Mono; margin-left: 25px; margin-right: 25px; margin-top: 15px; margin-bottom: 20px">
    The dataset for this competition (both train and test) was generated from a deep learning model trained on the <a href="https://www.kaggle.com/datasets/saurabhshahane/predicting-heat-flux">Predicting Critical Heat Flux</a> dataset. Feature distributions are close to, but not exactly the same, as the original. Feel free to use the original dataset as part of this competition, both to explore differences as well as to see whether incorporating the original in training improves model performance.
</p>
<b><span style="font-size:20px; font-family:JetBrains Mono; margin-left: 5px;">
    Task 🕵
</span></b>
<p style="font-size:16px;font-family: JetBrains Mono; margin-left: 25px; margin-right: 25px; margin-top: 15px; margin-bottom: 20px">
    
</p>
<b><span style="font-size:20px;font-family:JetBrains Mono; margin-left: 5px;">
    This Notebook Covers 📔
</span></b>
<ul style="font-size:16px; font-family: JetBrains Mono; margin-left: 10px; margin-right: 15px; margin-top: 15px; margin-bottom: 20px">
    <li></li>
</ul>
<b><span style="font-size:20px;font-family:JetBrains Mono; margin-left: 5px;">
    See More Here 📈
</span></b>
<p style="font-size:16px; font-family: JetBrains Mono; margin-left: 25px; margin-right: 25px; margin-top: 15px; margin-bottom: 20px">
    
</p>

# <p style="padding:15px; background-color:#2D3142; font-family:JetBrains Mono; font-weight:bold; color:#f2f2f0; font-size:100%; letter-spacing: 2px; text-align:center; border-radius: 10px 10px">EDA</p>

<p style="font-size:20px; font-family:JetBrains Mono; border-bottom: 3px solid #FF7F51; margin-left: 5px; margin-right: 5px;"><b>Notes</b> 📜</p>
<ul style="font-size:16px; font-family:JetBrains Mono; margin-right: 10px; margin-top: 2px; margin-bottom: 2px">
    <li></li>
</ul>

In [2]:
competition = "playground-series-s3e15"

if not ON_KAGGLE:
    download_competition_from_kaggle(competition)
    data_path = "data/data.csv"
else:
    data_path = f"/kaggle/input/{competition}/data.csv"

data = pd.read_csv(data_path, index_col="id")


In [3]:
data.head()


author geometry  pressure [MPa]  mass_flux [kg/m2-s]  x_e_out [-]  \
id                                                                        
0   Thompson     tube            7.00               3770.0       0.1754   
1   Thompson     tube             NaN               6049.0      -0.0416   
2   Thompson      NaN           13.79               2034.0       0.0335   
3       Beus  annulus           13.79               3679.0      -0.0279   
4        NaN     tube           13.79                686.0          NaN   

    D_e [mm]  D_h [mm]  length [mm]  chf_exp [MW/m2]  
id                                                    
0        NaN      10.8        432.0              3.6  
1       10.3      10.3        762.0              6.2  
2        7.7       7.7        457.0              2.5  
3        5.6      15.2       2134.0              3.0  
4       11.1      11.1        457.0              2.8

In [4]:
data.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 31644 entries, 0 to 31643
Data columns (total 9 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   author               26620 non-null  object 
 1   geometry             26144 non-null  object 
 2   pressure [MPa]       27192 non-null  float64
 3   mass_flux [kg/m2-s]  26853 non-null  float64
 4   x_e_out [-]          21229 non-null  float64
 5   D_e [mm]             26156 non-null  float64
 6   D_h [mm]             27055 non-null  float64
 7   length [mm]          26885 non-null  float64
 8   chf_exp [MW/m2]      31644 non-null  float64
dtypes: float64(7), object(2)
memory usage: 2.4+ MB


In [5]:
data.describe().T.rename(columns=str.title).style.background_gradient(DF_CMAP)


In [6]:
categories_only = data.select_dtypes(object).columns
numeric_only = data.select_dtypes("number").columns

data_cp = data.copy()
data_cp["x_e_out_missing"] = data_cp["x_e_out [-]"].isna().astype(bool)
data["x_e_out_missing"] = data["x_e_out [-]"].isna().map({False: "False", True: "True"})


In [7]:
fig = px.pie(
    data,
    names="x_e_out_missing",
    height=520,
    width=840,
    hole=0.65,
    title="Imputation Target Overview - x_e_out [-]",
    color_discrete_sequence=["#2D3142", "#FF7F51"],
)
fig.update_layout(
    font_color=FONT_COLOR,
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=False,
)
fig.add_annotation(
    dict(
        x=0.5,
        y=0.5,
        align="center",
        xref="paper",
        yref="paper",
        showarrow=False,
        font_size=22,
        text="Missing Values",
    )
)
fig.update_traces(
    hovertemplate=None,
    textposition="outside",
    textinfo="percent+label",
    textfont_size=16,
    rotation=20,
    marker_line_width=15,
    marker_line_color=BACKGROUND_COLOR,
)
fig.show()


In [8]:
fig = px.scatter_matrix(
    data,
    dimensions=numeric_only,
    color="x_e_out_missing",
    color_discrete_sequence=["#2D3142", "#FF7F51"],
    symbol_sequence=["x-thin", "cross-thin"],
    opacity=0.2,
    title="Numerical Features - Scatter Pair Plots",
    width=840,
    height=840,
)
fig.update_traces(
    diagonal_visible=False,
    showupperhalf=False,
    marker_size=1,
)
fig.update_layout(
    font_color=FONT_COLOR,
    font_size=9,
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=True,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        xanchor="right",
        y=1,
        x=1,
        itemsizing="constant",
    ),
)
fig.show()


In [47]:
col_names_map = {
    "mean": "X_e_out Missing Rate",
    "sum": "Missing Values",
    "count": "Total Values",
}

numeric_pivots = []

for feature in numeric_only:
    pivot = (
        data_cp.pivot_table(
            values="x_e_out_missing",
            index=pd.cut(data_cp[feature], 5),  # type: ignore
            aggfunc=["mean", "sum", "count"],
            margins=True,
            margins_name="Total",
        )
        .rename(columns=col_names_map)
        .droplevel(level=1, axis="columns")
        .style.background_gradient(DF_CMAP)  # type: ignore
        .set_table_attributes("style='display:inline'")
    )
    numeric_pivots.append(pivot)


In [41]:
display_html(numeric_pivots[0]._repr_html_() + numeric_pivots[1]._repr_html_(), raw=True)


X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 pressure [MPa] 
   
   
   
 
 
 
 
 (0.0794, 4.216] 
 0.324435 
 790 
 2435 
 
 
 (4.216, 8.332] 
 0.330583 
 2644 
 7998 
 
 
 (8.332, 12.448] 
 0.322312 
 1355 
 4204 
 
 
 (12.448, 16.564] 
 0.332332 
 3650 
 10983 
 
 
 (16.564, 20.68] 
 0.324427 
 510 
 1572 
 
 
 Total 
 0.329130 
 10415 
 31644 
 
 
 

 
 
 
   
 X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 mass_flux [kg/m2-s] 
   
   
   
 
 
 
 
 (-7.975, 1595.0] 
 0.324289 
 2474 
 7629 
 
 
 (1595.0, 3190.0] 
 0.333859 
 2542 
 7614 
 
 
 (3190.0, 4785.0] 
 0.334674 
 2330 
 6962 
 
 
 (4785.0, 6380.0] 
 0.326328 
 1087 
 3331 
 
 
 (6380.0, 7975.0] 
 0.317388 
 418 
 1317 
 
 
 Total 
 0.329130 
 10415 
 31644

In [42]:
display_html(numeric_pivots[2]._repr_html_() + numeric_pivots[3]._repr_html_(), raw=True)


X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 x_e_out [-] 
   
   
   
 
 
 
 
 (-0.868, -0.647] 
 0.000000 
 0 
 10 
 
 
 (-0.647, -0.427] 
 0.000000 
 0 
 81 
 
 
 (-0.427, -0.207] 
 0.000000 
 0 
 513 
 
 
 (-0.207, 0.0123] 
 0.000000 
 0 
 10952 
 
 
 (0.0123, 0.232] 
 0.000000 
 0 
 9673 
 
 
 Total 
 0.329130 
 10415 
 31644 
 
 
 

 
 
 
   
 X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 D_e [mm] 
   
   
   
 
 
 
 
 (0.964, 8.3] 
 0.322975 
 4282 
 13258 
 
 
 (8.3, 15.6] 
 0.330941 
 3919 
 11842 
 
 
 (15.6, 22.9] 
 0.353383 
 47 
 133 
 
 
 (22.9, 30.2] 
 0.341906 
 226 
 661 
 
 
 (30.2, 37.5] 
 0.358779 
 94 
 262 
 
 
 Total 
 0.329130 
 10415 
 31644

In [43]:
display_html(numeric_pivots[4]._repr_html_() + numeric_pivots[5]._repr_html_(), raw=True)


X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 D_h [mm] 
   
   
   
 
 
 
 
 (0.881, 24.8] 
 0.331308 
 8126 
 24527 
 
 
 (24.8, 48.6] 
 0.327832 
 576 
 1757 
 
 
 (96.2, 120.0] 
 0.325551 
 251 
 771 
 
 
 Total 
 0.329130 
 10415 
 31644 
 
 
 (48.6, 72.4] 
 nan 
 0 
 0 
 
 
 (72.4, 96.2] 
 nan 
 0 
 0 
 
 
 

 
 
 
   
 X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 length [mm] 
   
   
   
 
 
 
 
 (6.962, 617.6] 
 0.323841 
 4469 
 13800 
 
 
 (617.6, 1225.2] 
 0.333188 
 2285 
 6858 
 
 
 (1225.2, 1832.8] 
 0.311695 
 653 
 2095 
 
 
 (1832.8, 2440.4] 
 0.340237 
 1265 
 3718 
 
 
 (2440.4, 3048.0] 
 0.340580 
 141 
 414 
 
 
 Total 
 0.329130 
 10415 
 31644

In [13]:
corr = data.corr(numeric_only=True).round(2)
mask = np.triu(np.ones_like(corr, dtype=bool))
masked_corr = (
    corr.mask(mask).dropna(axis="index", how="all").dropna(axis="columns", how="all")
)

heatmap = go.Heatmap(
    z=masked_corr,
    x=masked_corr.columns,
    y=masked_corr.index,
    text=masked_corr.fillna(""),
    texttemplate="%{text}",
    xgap=10,
    ygap=10,
    showscale=True,
    colorscale=[[0.0, "#2D3142"], [0.5, "#8C92AC"], [1.0, "#FF7F51"]],
    colorbar_len=1.02,
    hoverinfo="none",
)
fig = go.Figure(heatmap)
fig.update_layout(
    font_color=FONT_COLOR,
    title="Correlation Matrix - Lower Triangular",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    width=840,
    height=840,
    xaxis_showgrid=False,
    yaxis_showgrid=False,
    yaxis_autorange="reversed",
)
fig.show()


In [14]:
from itertools import product
from scipy.stats import gaussian_kde


grid_size = 3
rows = cols = len(list(numeric_only)) // grid_size + 1
row = col = range(1, 4)
axes = list(product(row, col))

fig1 = make_subplots(
    rows=rows,
    cols=cols,
    y_title="Probability Density",
    horizontal_spacing=0.1,
    vertical_spacing=0.1,
)
fig2 = make_subplots(
    rows=rows,
    cols=cols,
    y_title="Probability Density",
    horizontal_spacing=0.1,
    vertical_spacing=0.1,
)

for (row, col), feature in zip(axes, numeric_only):
    feature_kde = gaussian_kde(data[feature].dropna())
    kde_range = np.linspace(
        data[feature].min() - data[feature].max() // 10,
        data[feature].max() + data[feature].max() // 10,
        len(data) // 10,
    )
    kde_estimated = feature_kde.evaluate(kde_range)
    kde_estimated_cumulative = np.cumsum(kde_estimated)
    kde_estimated_cumulative /= kde_estimated_cumulative.max()

    for fig, kde_data in zip((fig1, fig2), (kde_estimated, kde_estimated_cumulative)):
        fig.add_scatter(
            x=kde_range,
            y=kde_data,
            line=dict(dash="solid", color="#2D3142", width=2),
            # fill="tozeroy",
            name=feature,
            showlegend=False,
            row=row,
            col=col,
        )
        fig.update_xaxes(title_text=feature, row=row, col=col)

title1 = "Numerical Features - Kernel Density Estimation"
title2 = "Numerical Features - Cumulative Kernel Density Estimation"

for fig, title in zip((fig1, fig2), (title1, title2)):
    fig.update_layout(
        font_color=FONT_COLOR,
        title=title,
        title_font_size=18,
        plot_bgcolor=BACKGROUND_COLOR,
        paper_bgcolor=BACKGROUND_COLOR,
        width=840,
        height=840,
    )
    fig.update_annotations(font_size=14)


In [15]:
fig1.show()


In [16]:
fig2.show()


In [18]:
from scipy.stats import probplot


fig = make_subplots(
    rows=rows,
    cols=cols,
    y_title="Observed Values",
    x_title="Theoretical Quantiles",
    subplot_titles=numeric_only.to_list(),
    horizontal_spacing=0.1,
    vertical_spacing=0.1,
)

fig.update_annotations(font_size=14)

for (row, col), feature in zip(axes, numeric_only):
    data_sampled = data[feature].dropna().sample(2000, random_state=42)
    (osm, osr), (slope, intercept, R) = probplot(data_sampled, rvalue=True)
    x_theory = np.array([osm[0], osm[-1]])
    y_theory = intercept + slope * x_theory
    R2 = f"R2={R * R:.3f}"
    fig.add_scatter(x=osm, y=osr, mode="markers", row=row, col=col, name=feature)
    fig.add_scatter(x=x_theory, y=y_theory, mode="lines", row=row, col=col)
    fig.add_annotation(
        x=-1.5, y=osr[-1] * 0.75, text=R2, showarrow=False, row=row, col=col
    )

fig.update_layout(
    font_color=FONT_COLOR,
    title="Numerical Features - Probability Plots (Sampled within 2000 Observations)",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=False,
    width=840,
    height=840,
)
fig.update_traces(
    marker=dict(size=1, symbol="x-thin", line=dict(width=2, color="#2D3142")),
    line_color="#FF7F51",
)
fig.show()


In [79]:
fig = make_subplots(rows=1, cols=2, y_title="Count", horizontal_spacing=0.1)
fig.update_annotations(font_size=14)

for (row, col), feature in zip(((1, 1), (1, 2)), categories_only):
    if row == 1 and col == 1:
        showlegend = True
    else:
        showlegend = False
    fig.add_histogram(
        x=data.query("x_e_out_missing == 'True'")[feature],
        name="True",
        marker_color="#FF7F51",
        showlegend=showlegend,
        row=row,
        col=col,
    )
    fig.add_histogram(
        x=data.query("x_e_out_missing == 'False'")[feature],
        name="False",
        marker_color="#2D3142",
        showlegend=showlegend,
        row=row,
        col=col,
    )
    fig.update_xaxes(
        categoryorder="total ascending", title_text=feature, row=row, col=col
    )

fig.update_layout(
    font_color=FONT_COLOR,
    title="Categorical Features Overview",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    bargap=0.2,
    bargroupgap=0.1,
    width=840,
    height=540,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        xanchor="right",
        y=1.05,
        x=1,
        title="x_e_out_missing",
    ),
)
fig.show()


In [77]:
category_pivots = []

for feature in categories_only:
    pivot = (
        data_cp.pivot_table(
            values="x_e_out_missing",
            index=feature,
            aggfunc=["mean", "sum", "count"],
            margins=True,
            margins_name="Total",
        )
        .rename(columns=col_names_map)
        .droplevel(level=1, axis="columns")
        .style.background_gradient(DF_CMAP)  # type: ignore
        .set_table_attributes("style='display:inline'")
    )
    category_pivots.append(pivot)

display_html(category_pivots[0]._repr_html_() + category_pivots[1]._repr_html_(), raw=True)

X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 author 
   
   
   
 
 
 
 
 Beus 
 0.322319 
 517 
 1604 
 
 
 Inasaka 
 0.391304 
 18 
 46 
 
 
 Janssen 
 0.320324 
 870 
 2716 
 
 
 Kossolapov 
 0.306931 
 31 
 101 
 
 
 Mortimore 
 0.340102 
 67 
 197 
 
 
 Peskov 
 0.327491 
 355 
 1084 
 
 
 Richenderfer 
 0.319266 
 174 
 545 
 
 
 Thompson 
 0.331973 
 5775 
 17396 
 
 
 Weatherhead 
 0.325000 
 663 
 2040 
 
 
 Williams 
 0.363636 
 324 
 891 
 
 
 Total 
 0.330353 
 8794 
 26620 
 
 
 

 
 
 
   
 X_e_out Missing Rate 
 Missing Values 
 Total Values 
 
 
 geometry 
   
   
   
 
 
 
 
 annulus 
 0.321844 
 1410 
 4381 
 
 
 plate 
 0.313916 
 194 
 618 
 
 
 tube 
 0.332183 
 7024 
 21145 
 
 
 Total 
 0.330018 
 8628 
 26144